# AI-Powered News Digest Dynamo 📰✨
## Tame the News Flood with AI!
## [Hugging Space Demo of AI-Powered News Digest Dynamo 🔗🤗](https://huggingface.co/spaces/Kakaarot/AI-Powered-News-Digest-Dynamo)

## Motivation
In an era of information overload, staying updated with relevant news is challenging. This AI-Powered News Summarization System fetches, analyzes, and summarizes recent news articles on user-specified topics, delivering concise, structured insights. By leveraging advanced Gen AI, it empowers users to stay informed efficiently, addressing the real-world problem of navigating vast news streams.

### What it is?

My capstone project is an AI-powered News Summarization System that fetches and analyzes recent news articles on user-specified topics, then generates concise, structured summaries. This project addresses the problem of information overload by using advanced AI techniques to extract and present key information from multiple news sources in a unified, digestible format.

### Problem Statement :

This project addresses the problem of information overload by using advanced AI techniques to extract and present key information from multiple news sources in a unified, digestible format.

### System Workflow
The system:
- Fetches relevant news articles via NewsAPI based on user topics.
- Processes and chunks articles for embedding.
- Creates vector representations using SentenceTransformer.
- Builds a searchable FAISS index for semantic retrieval.
- Retrieves the most relevant information for a query.
- Generates a structured JSON summary with key points and sources.



### GenAI Capabilities Demonstrated
In my Kaggle notebook, I demonstrated the following GenAI capabilities:

1. **Retrieval Augmented Generation (RAG)** - The system implements a complete RAG pipeline that first retrieves relevant information from the news articles before generating summaries. This ensures the summaries are based on actual, recent news content rather than the model's internal knowledge.

2. **Document Understanding** - The system analyzes multiple news articles, extracts their key information, and synthesizes a coherent summary that captures the most important points across sources. The code demonstrates sophisticated document comprehension capabilities through the Gemini model.

3. **Structured Output/JSON mode** - I implemented controlled generation by using Gemini's response_mime_type="application/json" parameter and a defined JSON schema to enforce a consistent output structure. The system produces well-formatted JSON with predefined fields for topic, summary points, and sources.

4. **Embeddings** - The project uses SentenceTransformer to create dense vector embeddings of text chunks, enabling semantic understanding and comparison of content.

5. **Vector Search/Vector Store** - I implemented a vector database using FAISS to index and efficiently search through text embeddings, allowing the system to find the most semantically relevant information based on user queries.

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))
        
os.environ["CUDA_VISIBLE_DEVICES"] = ""  # Disable GPU to avoid CUDA conflicts

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

This notebook demonstrates a comprehensive news summarization system using Retrieval Augmented Generation (RAG), Document Understanding, and Structured Output capabilities. The system fetches recent news articles based on user topics, processes them using embeddings and vector search, and generates concise, structured summaries.

## 1. Setup and Installation

Installs libraries:
- `newsapi-python`: Fetches news articles.
- `sentence-transformers`: Generates text embeddings.
- `faiss-cpu`: Enables vector search.
- `google-generativeai`: Powers Gemini for summarization.

In [2]:
!pip install newsapi-python sentence-transformers faiss-cpu google-generativeai --quiet


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.7/30.7 MB 48.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 28.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 31.2 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pylibcugraph-cu12 24.12.0 requires pylibraft-cu12==24.12.*, but you have pylibraft-cu12 25.2.0 which is incompatible.
pylibcugraph-cu12 24.12.0 requires rmm-cu12==24.12.*, but you have rm

let's import the required libraries and configure our API keys:

In [3]:
import os
import json
import faiss
import numpy as np
import google.generativeai as genai
from newsapi import NewsApiClient
from sentence_transformers import SentenceTransformer
from typing import List, Dict, Any, Optional

# For Kaggle environment, use Kaggle secrets
from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
secret_value_0 = user_secrets.get_secret("GOOGLE_API_KEY")
secret_value_1 = user_secrets.get_secret("NEWS_API_KEY")

GOOGLE_API_KEY = secret_value_0
NEWS_API_KEY = secret_value_1 

# Validate API keys
if not NEWS_API_KEY:
    raise ValueError("Please set the NEWS_API_KEY in Kaggle secrets.")
if not GOOGLE_API_KEY:
    raise ValueError("Please set the GEMINI_API_KEY in Kaggle secrets.")

# Configure Google Generative AI
genai.configure(api_key=GOOGLE_API_KEY)

# Constants
EMBEDDING_MODEL_NAME = 'all-MiniLM-L6-v2'  # Lightweight, efficient embedding model
LLM_MODEL_NAME = 'gemini-1.5-flash'        # Efficient Gemini model
MAX_ARTICLES_TO_FETCH = 10                 # Max news articles to retrieve initially
MAX_ARTICLES_TO_PROCESS = 5                # Max articles to use for context
CHUNK_SIZE = 500                           # Characters per text chunk
TOP_K_CHUNKS = 3                           # Number of relevant chunks to retrieve


2025-04-21 04:43:39.120223: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1745210619.398532      13 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1745210619.474587      13 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


## 2. News Retrieval Function

**The first component of our system fetches news articles related to a user's topic of interest:**

In [4]:
def fetch_news(topic: str) -> List[Dict[str, Any]]:
    """Fetches recent news articles for a given topic using NewsAPI."""
    print(f"Fetching news for topic: {topic}...")
    try:
        newsapi = NewsApiClient(api_key=NEWS_API_KEY)
        # Fetch articles related to the topic
        top_headlines = newsapi.get_everything(
            q=topic,
            language='en',
            sort_by='relevancy',  # Can also use 'publishedAt' for recency
            page_size=MAX_ARTICLES_TO_FETCH
        )

        articles = top_headlines.get('articles', [])
        # Filter out articles with no content
        valid_articles = [
            {
                "title": article.get("title"),
                "content": article.get("content") or article.get("description", ""), 
                "url": article.get("url")
            }
            for article in articles if article.get("content") or article.get("description")
        ]
        print(f"Fetched {len(valid_articles)} valid articles.")
        # Limit the number of articles to process further
        return valid_articles[:MAX_ARTICLES_TO_PROCESS]
    except Exception as e:
        print(f"Error fetching news: {e}")
        return []


## 3. Text Processing Functions

Next, we need functions to process the text for our RAG system:

In [5]:
def chunk_text(text: str, size: int) -> List[str]:
    """Splits text into chunks of approximate size, trying to preserve sentence boundaries."""
    chunks = []
    start = 0
    while start < len(text):
        end = start + size
        # Try to end chunk at a sentence boundary if possible
        pos = text.rfind('.', start, end + 50)  # Look a bit beyond chunk size
        if pos != -1 and pos > start + size // 2:  # Ensure boundary is reasonably close
            end = pos + 1
        chunks.append(text[start:end].strip())
        start = end
    return [chunk for chunk in chunks if chunk]  # Remove empty chunks

def build_vector_store(articles: List[Dict[str, Any]], model: SentenceTransformer):
    """Creates embeddings and builds an in-memory FAISS index."""
    print("Building vector store...")
    all_chunks = []
    metadata = []  # Store corresponding article info for each chunk

    for i, article in enumerate(articles):
        if article['content']:
            chunks = chunk_text(article['content'], CHUNK_SIZE)
            for chunk in chunks:
                all_chunks.append(chunk)
                metadata.append({"article_index": i, "url": article['url'], "title": article['title']})

    if not all_chunks:
        print("No text content found to build vector store.")
        return None, [], []

    print(f"Generated {len(all_chunks)} chunks from {len(articles)} articles.")
    print("Creating embeddings...")
    embeddings = model.encode(all_chunks, show_progress_bar=True)

    dimension = embeddings.shape[1]
    index = faiss.IndexFlatL2(dimension)  # Using L2 distance for similarity
    index.add(np.array(embeddings).astype('float32'))  # Add embeddings to FAISS index

    print("Vector store built successfully.")
    return index, all_chunks, metadata


## 4. Retrieval Function (RAG)

This function performs the retrieval part of RAG, finding the most relevant chunks for a query:

In [6]:
def retrieve_context(query: str, index: faiss.Index, chunks: List[str], metadata: List[Dict], model: SentenceTransformer, top_k: int) -> str:
    """Retrieves the most relevant text chunks based on the query."""
    if index is None or index.ntotal == 0:
        return "No relevant context found (vector store is empty)."

    print(f"Retrieving top {top_k} relevant chunks for query: '{query}'...")
    query_embedding = model.encode([query], show_progress_bar=False)
    query_embedding_np = np.array(query_embedding).astype('float32')

    # Search the index
    distances, indices = index.search(query_embedding_np, top_k)

    # Gather the relevant chunks and source info
    context_parts = []
    seen_urls = set()
    for i, idx in enumerate(indices[0]):
        if idx >= 0 and idx < len(chunks):  # Check for valid index
            chunk_text = chunks[idx]
            meta = metadata[idx]
            source_info = f"(Source: {meta['url']})"
            if meta['url'] not in seen_urls:
                 # Add title for first mention of a source URL
                 context_parts.append(f"From '{meta['title']}':\n{chunk_text}\n{source_info}")
                 seen_urls.add(meta['url'])
            else:
                # Avoid repeating title for subsequent chunks from same source
                context_parts.append(f"{chunk_text}\n{source_info}")

    if not context_parts:
        return "No relevant context found matching the query."

    print("Retrieved relevant context.")
    return "\n\n".join(context_parts)


## 5. Summary Generation Function (Document Understanding + Structured Output)

This function uses the LLM to understand the retrieved documents and generate a structured summary:

In [7]:
def generate_structured_summary(context: str, topic: str) -> Optional[Dict[str, Any]]:
    """Generates a summary using an LLM with structured output request."""
    print("Generating structured summary with LLM...")
    model = genai.GenerativeModel(LLM_MODEL_NAME)

    # Define the desired JSON structure
    json_schema = {
        "type": "object",
        "properties": {
            "topic": {"type": "string", "description": "The main topic summarized."},
            "summary_points": {
                "type": "array",
                "items": {"type": "string"},
                "description": "A list of key points summarizing the context."
            },
            "mentioned_sources": {
                 "type": "array",
                 "items": {"type": "string", "format": "uri"},
                 "description": "List of unique source URLs mentioned in the context provided."
            }
        },
        "required": ["topic", "summary_points", "mentioned_sources"]
    }

    prompt = f"""
    Based ONLY on the following retrieved context about '{topic}', provide a concise summary.
    Extract the key points and list the unique source URLs mentioned.
    Respond ONLY with a valid JSON object matching the following schema:

    Schema:
    {json.dumps(json_schema, indent=2)}

    Retrieved Context:
    ---
    {context}
    ---

    JSON Output:
    """

    try:
        response = model.generate_content(
            prompt,
            generation_config=genai.types.GenerationConfig(
                 response_mime_type="application/json"  # Request JSON output
            )
        )
        # The API should return validated JSON directly when using response_mime_type
        summary_json = json.loads(response.text)
        print("LLM generation successful.")
        return summary_json
    except Exception as e:
        print(f"Error during LLM generation or JSON parsing: {e}")
        # Attempt to see if there's partial text in case of error
        try:
            print(f"LLM Raw Response Text (if available): {response.text}")
        except:
            pass
        return None


## 6. Main Execution Function

Now, let's put everything together in a main function:

In [8]:
def main():
    # 1. Load Embedding Model
    print("Loading embedding model...")
    try:
        embedding_model = SentenceTransformer(EMBEDDING_MODEL_NAME)
    except Exception as e:
        print(f"Error loading Sentence Transformer model '{EMBEDDING_MODEL_NAME}': {e}")
        print("Please ensure the model is available or try a different one.")
        return

    # 2. Get User Topic
    user_topic = "Akira Toriyama"
    if not user_topic:
        print("No topic entered. Exiting.")
        return

    # 3. Fetch News Articles
    articles = fetch_news(user_topic)
    if not articles:
        print(f"Could not fetch any news articles for '{user_topic}'.")
        return

    # 4. Build Vector Store (Embeddings + FAISS Index) - RAG Part 1
    vector_index, text_chunks, chunk_metadata = build_vector_store(articles, embedding_model)

    if vector_index is None:
        print("Failed to build vector store. Cannot proceed with retrieval.")
        return

    # 5. Retrieve Relevant Context (Similarity Search) - RAG Part 2
    retrieved_context = retrieve_context(user_topic, vector_index, text_chunks, chunk_metadata, embedding_model, TOP_K_CHUNKS)

    # 6. Generate Structured Summary (Document Understanding + Structured Output)
    if "No relevant context found" in retrieved_context:
        print("Could not find specific context matching the query within the fetched articles.")
        summary_output = {"topic": user_topic, "summary_points": ["Could not retrieve specific context. General news might be available but not summarized via RAG."], "mentioned_sources": [a['url'] for a in articles]}
    else:
        summary_output = generate_structured_summary(retrieved_context, user_topic)

    # 7. Display Result
    print("\n--- Generated News Digest ---")
    if summary_output:
        print(json.dumps(summary_output, indent=2))
    else:
        print("Failed to generate summary.")
    print("---------------------------\n")

if __name__ == "__main__":
    main()


Loading embedding model...


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Fetching news for topic: Akira Toriyama...
Fetched 10 valid articles.
Building vector store...
Generated 5 chunks from 5 articles.
Creating embeddings...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Vector store built successfully.
Retrieving top 3 relevant chunks for query: 'Akira Toriyama'...
Retrieved relevant context.
Generating structured summary with LLM...
LLM generation successful.

--- Generated News Digest ---
{
  "topic": "Akira Toriyama and the Dragon Ball Franchise",
  "summary_points": [
    "Akira Toriyama's Dragon Ball franchise includes the recently concluded Dragon Ball Daima (20 episodes).",
    "The Dragon Ball manga significantly influenced the action shonen genre.",
    "The franchise primarily focuses on Goku's story, although other characters like Gohan and Vegeta have had prominent roles."
  ],
  "mentioned_sources": [
    "https://screenrant.com/dragon-ball-daima-rank-franchise-op-ed/",
    "https://www.ign.com/articles/dragon-ball-anime-and-movies-in-order",
    "https://screenrant.com/dragon-ball-anime-movie-vegeta-main-character-theory/"
  ]
}
---------------------------



## 7. Example Usage and Output

Let's run the system with a sample topic:

In [9]:
# For demonstration, we'll run the main function
main()


Loading embedding model...
Fetching news for topic: Akira Toriyama...
Fetched 10 valid articles.
Building vector store...
Generated 5 chunks from 5 articles.
Creating embeddings...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Vector store built successfully.
Retrieving top 3 relevant chunks for query: 'Akira Toriyama'...
Retrieved relevant context.
Generating structured summary with LLM...
LLM generation successful.

--- Generated News Digest ---
{
  "topic": "Akira Toriyama and the Dragon Ball Franchise",
  "summary_points": [
    "Akira Toriyama's Dragon Ball franchise concluded its latest installment, Dragon Ball Daima, after 20 episodes.",
    "The Dragon Ball franchise, a manga by Akira Toriyama, significantly influenced the action shonen manga genre.",
    "Discussions about the franchise often center on Goku as the main character, with some suggesting Vegeta should take the lead in future installments."
  ],
  "mentioned_sources": [
    "https://screenrant.com/dragon-ball-daima-rank-franchise-op-ed/",
    "https://www.ign.com/articles/dragon-ball-anime-and-movies-in-order",
    "https://screenrant.com/dragon-ball-anime-movie-vegeta-main-character-theory/"
  ]
}
---------------------------



Example output:

In [10]:
'''
Enter the news topic you want to summarize (e.g., 'AI advancements in healthcare'): Football
Fetching news for topic: Football...
Fetched 10 valid articles.
Building vector store...
Generated 5 chunks from 5 articles.
Creating embeddings...
Batches: 100% 1/1 [00:00<00:00, 4.81it/s]
Vector store built successfully.
Retrieving top 3 relevant chunks for query: 'Football'...
Retrieved relevant context.
Generating structured summary with LLM...
LLM generation successful.

--- Generated News Digest ---
{
  "topic": "Football",
  "summary_points": [
    "The NFL is using Sony's Hawk-Eye cameras to track the ball's position.",
    "Thomas Tuchel's tenure as England's coach is still in its early stages.",
    "A long-time Wigan Athletic supporter, known as 'Mr Wigan Athletic,' passed away."
  ],
  "mentioned_sources": [
    "https://www.theverge.com/news/640890/nfl-sony-hawk-eye-first-down-chains",
    "https://www.bbc.com/sport/football/articles/cvged6573dmo",
    "https://www.bbc.com/sport/football/articles/c241e8gvz9eo"
  ]
}
---------------------------
'''

'\nEnter the news topic you want to summarize (e.g., \'AI advancements in healthcare\'): Football\nFetching news for topic: Football...\nFetched 10 valid articles.\nBuilding vector store...\nGenerated 5 chunks from 5 articles.\nCreating embeddings...\nBatches: 100% 1/1 [00:00<00:00, 4.81it/s]\nVector store built successfully.\nRetrieving top 3 relevant chunks for query: \'Football\'...\nRetrieved relevant context.\nGenerating structured summary with LLM...\nLLM generation successful.\n\n--- Generated News Digest ---\n{\n  "topic": "Football",\n  "summary_points": [\n    "The NFL is using Sony\'s Hawk-Eye cameras to track the ball\'s position.",\n    "Thomas Tuchel\'s tenure as England\'s coach is still in its early stages.",\n    "A long-time Wigan Athletic supporter, known as \'Mr Wigan Athletic,\' passed away."\n  ],\n  "mentioned_sources": [\n    "https://www.theverge.com/news/640890/nfl-sony-hawk-eye-first-down-chains",\n    "https://www.bbc.com/sport/football/articles/cvged6573dmo

## 8. Technical Details and GenAI Capabilities

This system demonstrates three key GenAI capabilities:

### 8.1 Retrieval Augmented Generation (RAG)

- **Embeddings:** We use the SentenceTransformer model to convert text chunks into dense vector representations.

- **Vector Store:** FAISS provides efficient similarity search capabilities for our embeddings.

- **Retrieval Process:** The system embeds the user's query and finds the most semantically similar chunks from the news articles.

- **Context Augmentation:** The retrieved chunks are sent to the LLM to provide up-to-date, relevant context for generation.

### 8.2 Document Understanding

* The system processes and understands multiple news articles, identifying key information.

* It extracts the most important points from potentially complex news content.

* The LLM comprehends the context of the articles and synthesizes a coherent summary.

### 8.3 Structured Output / JSON Mode

- We define a specific JSON schema for the output format.

- The LLM is instructed to generate a response that strictly adheres to this structure.

- We use Gemini's response_mime_type="application/json" parameter to enforce JSON output.

- The result is a consistently structured, machine-readable summary that can be easily parsed and displayed.

### 8.4. Embeddings

- The system creates semantic vector representations of text:

- Uses the SentenceTransformer model (all-MiniLM-L6-v2) to encode text chunks into numerical vectors

- These embeddings capture the semantic meaning of each text chunk

- The build_vector_store function handles this conversion: embeddings = model.encode(all_chunks, show_progress_bar=True)

- Embeddings enable semantic similarity comparison rather than just keyword matching

### 8.5. Vector Search / Vector Store

- The system implements a vector database for efficient similarity search:

- Uses FAISS (faiss.IndexFlatL2) to create an in-memory vector index

- Stores embeddings in this index for efficient retrieval: index.add(np.array(embeddings).astype('float32'))

- Performs similarity search to find the most relevant content: distances, indices = index.search(query_embedding_np, top_k)

- This capability enables finding semantically similar content even when exact keywords don't match

## 9. Potential Improvements
This system could be enhanced in several ways:

1. Filtering by Date: Add date range parameters to focus on very recent news.

2. Source Diversity: Ensure summaries include diverse news sources for balanced reporting.

3. Multilingual Support: Extend the system to handle news in multiple languages.

4. Sentiment Analysis: Add sentiment detection to identify positive/negative news trends.

5. Topic Clustering: Group related news items together in the summary.

6. User Preferences: Allow users to save preferred topics and sources.

7. Web Interface: Create a simple UI for easier interaction with the system.

## 10. Conclusion

This notebook demonstrates a practical application of modern GenAI techniques to solve the problem of information overload in news consumption. By combining RAG, document understanding, and structured output capabilities, we've created a system that can efficiently summarize news on any topic, providing users with concise, relevant information from reliable sources.